# Set up imports

In [1]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [3]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [4]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [5]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [6]:
data = df.abstract.values.tolist()

In [7]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [8]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [9]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [10]:
# less than 10 documents,
id2word = corpora.Dictionary(data)
id2word.filter_extremes(no_below = 50)

In [11]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [12]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [13]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [14]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [15]:
ldaseq.print_topics(time=0) # at timeslice 1, those are the topics

[[('model', 0.02821009761261272),
  ('neural', 0.01642542195587268),
  ('neuron', 0.014263559300936672),
  ('network', 0.011844839938366096),
  ('stimulus', 0.011577149852333518),
  ('system', 0.011295281853915692),
  ('data', 0.010861822128167338),
  ('activity', 0.010419149409906143),
  ('response', 0.010090408754308),
  ('time', 0.009821022324318866),
  ('information', 0.009741224927213117),
  ('brain', 0.009413076729058995),
  ('spike', 0.009363342904973907),
  ('dynamic', 0.00896792002230647),
  ('show', 0.00838931025228542),
  ('signal', 0.007313468566134133),
  ('input', 0.006745398188789169),
  ('population', 0.006677612587145883),
  ('pattern', 0.006548228544068633),
  ('mechanism', 0.006397367273980292)],
 [('algorithm', 0.05392004216620926),
  ('problem', 0.03522901906206928),
  ('method', 0.024282779733371666),
  ('function', 0.023562612895876564),
  ('optimization', 0.019489638334130876),
  ('gradient', 0.015083211978649872),
  ('solution', 0.013391878709695174),
  ('conve

In [16]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('model', 0.02821009761261272),
  ('neural', 0.01642542195587268),
  ('neuron', 0.014263559300936672),
  ('network', 0.011844839938366096),
  ('stimulus', 0.011577149852333518),
  ('system', 0.011295281853915692),
  ('data', 0.010861822128167338),
  ('activity', 0.010419149409906143),
  ('response', 0.010090408754308),
  ('time', 0.009821022324318866),
  ('information', 0.009741224927213117),
  ('brain', 0.009413076729058995),
  ('spike', 0.009363342904973907),
  ('dynamic', 0.00896792002230647),
  ('show', 0.00838931025228542),
  ('signal', 0.007313468566134133),
  ('input', 0.006745398188789169),
  ('population', 0.006677612587145883),
  ('pattern', 0.006548228544068633),
  ('mechanism', 0.006397367273980292)],
 [('model', 0.028292425792884247),
  ('neural', 0.01625913917600432),
  ('neuron', 0.014334386515954816),
  ('network', 0.011791900634214269),
  ('stimulus', 0.011625469957069853),
  ('system', 0.011244411949130792),
  ('data', 0.010904785427150886),
  ('activity', 0.0104596

In [31]:
ldaseq.print_topic_times(1)

[[('algorithm', 0.05392004216620926),
  ('problem', 0.03522901906206928),
  ('method', 0.024282779733371666),
  ('function', 0.023562612895876564),
  ('optimization', 0.019489638334130876),
  ('gradient', 0.015083211978649872),
  ('solution', 0.013391878709695174),
  ('convex', 0.012141321736561305),
  ('convergence', 0.011481518903735626),
  ('show', 0.009755133251474143),
  ('approach', 0.009214485344779363),
  ('approximation', 0.008281197897903244),
  ('learning', 0.008271156555484584),
  ('stochastic', 0.00807220717157265),
  ('paper', 0.007880951981059306),
  ('descent', 0.007419518719602414),
  ('objective', 0.007244263778126095),
  ('result', 0.006526839624960571),
  ('also', 0.006163043790458918),
  ('based', 0.0060249406349884)],
 [('algorithm', 0.05407964579807812),
  ('problem', 0.03531530397773975),
  ('method', 0.02433459713314731),
  ('function', 0.023611693091854638),
  ('optimization', 0.019526888043023674),
  ('gradient', 0.015109250947423145),
  ('solution', 0.013412

In [18]:
ldaseq.print_topic_times(topic=2)

[[('model', 0.0734200689094094),
  ('inference', 0.026114773048402),
  ('data', 0.02357858469930664),
  ('latent', 0.016691218238439276),
  ('process', 0.01651040838469296),
  ('bayesian', 0.016189990391741384),
  ('variable', 0.013453882113103117),
  ('method', 0.013212132055093553),
  ('probabilistic', 0.012432872402663183),
  ('structure', 0.012087357078890765),
  ('approach', 0.011683808883617041),
  ('distribution', 0.01083771955883538),
  ('prior', 0.010272511136451107),
  ('mixture', 0.009035399608626074),
  ('topic', 0.00902880017256594),
  ('algorithm', 0.009009887861615027),
  ('variational', 0.008584940953929861),
  ('gaussian', 0.008295817256097331),
  ('using', 0.007724377333887839),
  ('present', 0.007416253239789008)],
 [('model', 0.0733338805387403),
  ('inference', 0.02621265401171934),
  ('data', 0.023663189948939244),
  ('latent', 0.016738620690346945),
  ('process', 0.016499634525680092),
  ('bayesian', 0.01623490590274653),
  ('variable', 0.013430705670263379),
  (

In [19]:
ldaseq.print_topic_times(topic=3)

[[('matrix', 0.03658659769568978),
  ('sparse', 0.035569038160465805),
  ('problem', 0.019624846988526744),
  ('algorithm', 0.01682296570427406),
  ('method', 0.012459495538911299),
  ('norm', 0.011611264787051859),
  ('data', 0.011533024077972995),
  ('analysis', 0.009746011926169718),
  ('linear', 0.009508455266173622),
  ('sparsity', 0.009483734172994947),
  ('show', 0.008874163808654457),
  ('result', 0.008610304520153282),
  ('signal', 0.008090524527727816),
  ('estimation', 0.007758914357102626),
  ('model', 0.007617473126670544),
  ('vector', 0.007615585600566472),
  ('number', 0.007380847775177788),
  ('regression', 0.007305266315462973),
  ('pca', 0.006676977500176704),
  ('component', 0.006537322447857546)],
 [('matrix', 0.03670849551812131),
  ('sparse', 0.035686870579083554),
  ('problem', 0.01967182091838921),
  ('algorithm', 0.01680491864152774),
  ('method', 0.012481926594039634),
  ('norm', 0.011631293279712476),
  ('data', 0.01155296310630552),
  ('analysis', 0.0097499

In [20]:
ldaseq.print_topic_times(topic=4)

[[('distribution', 0.03506394179931641),
  ('graph', 0.020679532960448995),
  ('sample', 0.017514247737361342),
  ('estimation', 0.014505287055019578),
  ('estimator', 0.013893921223543108),
  ('estimate', 0.013646398986912566),
  ('method', 0.012559865355257004),
  ('random', 0.01252830830069816),
  ('probability', 0.012472880547339606),
  ('test', 0.012002208340739921),
  ('density', 0.010394672562983015),
  ('model', 0.009437268507180116),
  ('data', 0.00896281654109684),
  ('sampling', 0.00844325620771423),
  ('show', 0.00797875782265204),
  ('likelihood', 0.007481567250255048),
  ('parameter', 0.007063375498930649),
  ('maximum', 0.006928450122735567),
  ('variable', 0.006673098997212391),
  ('based', 0.0065927913203933045)],
 [('distribution', 0.03515396457966042),
  ('graph', 0.020723658195584856),
  ('sample', 0.01754781478387054),
  ('estimation', 0.014530122398963438),
  ('estimator', 0.01391722681546277),
  ('estimate', 0.013668620285984763),
  ('method', 0.01257996557942751

In [21]:
ldaseq.print_topic_times(topic=5)

[[('learning', 0.02540738097007052),
  ('policy', 0.02087488234319336),
  ('problem', 0.02029107749720892),
  ('algorithm', 0.01732170051968217),
  ('state', 0.01567056582892768),
  ('decision', 0.014447850902794155),
  ('action', 0.012692668971044136),
  ('approach', 0.01127049396690185),
  ('show', 0.010853223050903272),
  ('search', 0.010380364728505273),
  ('reward', 0.009815541160508572),
  ('agent', 0.009532819942151534),
  ('control', 0.009277654308167542),
  ('reinforcement', 0.008828259320506238),
  ('value', 0.008624808026007616),
  ('game', 0.008472838456091489),
  ('optimal', 0.008370337867586472),
  ('model', 0.00835131156044025),
  ('function', 0.008196479829148232),
  ('process', 0.007607793811325777)],
 [('learning', 0.0254636062697616),
  ('policy', 0.020917518052200774),
  ('problem', 0.020332123418891627),
  ('algorithm', 0.017354881824848317),
  ('state', 0.015698003065984695),
  ('decision', 0.014472492903998926),
  ('action', 0.012712800454847453),
  ('approach', 

In [22]:
ldaseq.print_topic_times(topic=6)

[[('data', 0.03196158176708814),
  ('kernel', 0.02491969853647254),
  ('learning', 0.02463892837719151),
  ('method', 0.0228648062072461),
  ('algorithm', 0.016861285612746416),
  ('feature', 0.014793734946838626),
  ('clustering', 0.01425112459295212),
  ('problem', 0.012504235909021598),
  ('set', 0.010582660214817047),
  ('space', 0.009660358181560174),
  ('function', 0.009516702646219092),
  ('approach', 0.00915741757089059),
  ('show', 0.009124112330528603),
  ('regression', 0.009000072605076974),
  ('paper', 0.00832019247590618),
  ('task', 0.00816856688183402),
  ('proposed', 0.008001296902807414),
  ('metric', 0.007859279289629418),
  ('based', 0.007437972597641579),
  ('classification', 0.007374702992048083)],
 [('data', 0.03204221328092163),
  ('kernel', 0.024973157425605838),
  ('learning', 0.024694204759405765),
  ('method', 0.02291402018093638),
  ('algorithm', 0.016892290305715617),
  ('feature', 0.014818848736359497),
  ('clustering', 0.014274945188291206),
  ('problem',

In [23]:
ldaseq.print_topic_times(topic=7)

[[('network', 0.0390142836213492),
  ('training', 0.02405940546327065),
  ('learning', 0.023635640043984007),
  ('prediction', 0.013571317758291),
  ('deep', 0.013164736082272435),
  ('method', 0.0124454520135528),
  ('task', 0.011635290707350731),
  ('input', 0.011512500751461534),
  ('model', 0.011347780680707032),
  ('neural', 0.011342028264644062),
  ('performance', 0.010748255152354473),
  ('layer', 0.010409828743702483),
  ('feature', 0.010007393599003812),
  ('show', 0.009536389472690967),
  ('using', 0.008259340564232793),
  ('architecture', 0.007811561554264726),
  ('node', 0.00768423841267469),
  ('output', 0.007529720944733306),
  ('tree', 0.007435170513869035),
  ('machine', 0.007346568390632473)],
 [('network', 0.0388357484583641),
  ('training', 0.024068874940497725),
  ('learning', 0.023697633931630668),
  ('prediction', 0.013613272369759422),
  ('deep', 0.013203696773837302),
  ('method', 0.01248132187641144),
  ('task', 0.011667247855658409),
  ('input', 0.011455435945

In [24]:
ldaseq.print_topic_times(topic=8)

[[('algorithm', 0.036564451299272105),
  ('bound', 0.03449133586584717),
  ('learning', 0.026188870492262466),
  ('loss', 0.018081341871652716),
  ('problem', 0.012944505177257839),
  ('online', 0.012688492555688834),
  ('function', 0.012523792544750414),
  ('show', 0.01201492691798759),
  ('result', 0.011738009288678755),
  ('regret', 0.010494791379644403),
  ('case', 0.010167038577766218),
  ('class', 0.009650259827029183),
  ('complexity', 0.00946340757837505),
  ('setting', 0.009355410534006244),
  ('rate', 0.00856673864014218),
  ('error', 0.008564281415124626),
  ('risk', 0.008130527290825347),
  ('number', 0.007215835626465706),
  ('time', 0.006899989943700171),
  ('also', 0.006815786218048252)],
 [('algorithm', 0.03665763212774661),
  ('bound', 0.034578798183811404),
  ('learning', 0.02624573089957285),
  ('loss', 0.018114516862268205),
  ('problem', 0.01296386788346703),
  ('online', 0.012707667793485297),
  ('function', 0.01254265054090179),
  ('show', 0.012033118948613109),


In [25]:
ldaseq.print_topic_times(topic=9)

[[('image', 0.040968953268400284),
  ('model', 0.024630042925272135),
  ('object', 0.023297352408652133),
  ('feature', 0.016185964634583837),
  ('learning', 0.01526052674028643),
  ('task', 0.013463560210439669),
  ('approach', 0.012718793755824201),
  ('method', 0.009909051308779329),
  ('human', 0.009785772269370394),
  ('visual', 0.009700295309707122),
  ('representation', 0.009682032543611958),
  ('data', 0.008681563195408748),
  ('two', 0.007632964470505146),
  ('recognition', 0.007351892738565018),
  ('training', 0.007107845004516923),
  ('scene', 0.007057881182862835),
  ('set', 0.006753213238646683),
  ('using', 0.0066994158254770194),
  ('word', 0.006607311155526942),
  ('show', 0.006582388707432016)],
 [('image', 0.04063474112373163),
  ('model', 0.0247163569251449),
  ('object', 0.0232741185047215),
  ('feature', 0.016237811547281395),
  ('learning', 0.015299160899037595),
  ('task', 0.013500880695779082),
  ('approach', 0.012753756424176732),
  ('method', 0.009932046083357

In [26]:
# to check Document - Topic proportions, use `doc-topics`
doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
print (doc)
# this document is made up of different topics like this

[3.55871886e-04 3.55871886e-04 4.88825108e-01 3.55871886e-04
 1.92836945e-01 3.55871886e-04 3.55871886e-04 3.55871886e-04
 3.55871886e-04 3.15846844e-01]


In [27]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [28]:
ldaseq.print_topic_times(1) # evolution of values for first time slice


[[('algorithm', 0.05392004216620926),
  ('problem', 0.03522901906206928),
  ('method', 0.024282779733371666),
  ('function', 0.023562612895876564),
  ('optimization', 0.019489638334130876),
  ('gradient', 0.015083211978649872),
  ('solution', 0.013391878709695174),
  ('convex', 0.012141321736561305),
  ('convergence', 0.011481518903735626),
  ('show', 0.009755133251474143),
  ('approach', 0.009214485344779363),
  ('approximation', 0.008281197897903244),
  ('learning', 0.008271156555484584),
  ('stochastic', 0.00807220717157265),
  ('paper', 0.007880951981059306),
  ('descent', 0.007419518719602414),
  ('objective', 0.007244263778126095),
  ('result', 0.006526839624960571),
  ('also', 0.006163043790458918),
  ('based', 0.0060249406349884)],
 [('algorithm', 0.05407964579807812),
  ('problem', 0.03531530397773975),
  ('method', 0.02433459713314731),
  ('function', 0.023611693091854638),
  ('optimization', 0.019526888043023674),
  ('gradient', 0.015109250947423145),
  ('solution', 0.013412

In [29]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.7980240253453317
CV1 0.4372549291868467
U_Mass2 -1.7969200745300284
CV2 0.43725492918684666
U_Mass3 -1.7941790502133976
CV3 0.44053127073237164
U_Mass4 -1.810287361472792
CV4 0.4425487390001618
U_Mass5 -1.8438865461076535
CV5 0.44678404813359823
U_Mass6 -1.8729928420706372
CV6 0.4451555962409877
U_Mass7 -1.843917309910357
CV7 0.4434509665672367
U_Mass8 -1.802694077846175
CV8 0.43560567742610684
U_Mass9 -1.814448470608631
CV9 0.43762059152100524
U_Mass10 -1.7953977022773984
CV10 0.434043683442105
U_Mass11 -1.7733630014162223
CV11 0.4298501631184818
U_Mass12 -1.7744670267295373
CV12 0.43691614080803787


In [30]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/